In [2]:
from apscheduler.schedulers.blocking import BlockingScheduler
from oandapyV20 import API
import oandapyV20.endpoints.orders as orders
from oandapyV20.contrib.requests import MarketOrderRequest
from oanda_candles import Pair, Gran, CandleClient
from oandapyV20.endpoints.instruments import InstrumentsCandles
from oandapyV20.contrib.requests import TakeProfitDetails, StopLossDetails
import talib
import pandas_ta as ta
import numpy as np
import pandas as pd


In [3]:
def signal_generator(df):
    vwap = df['VWAP']
    rsi = df['RSI'].dropna()

    close_price = df['Close']
    upper_bb = df['UpperBB']
    lower_bb = df['LowerBB']
    average_rsi = rsi.mean()
    bullish = True
    bearish = True
    #print(rsi.values)
    for i in range(len(df)):
        if max(df['Open'][i], df['Close'][i]) >= df['VWAP'][i]:
            bearish = False
        if min(df['Open'][i], df['Close'][i]) <= df['VWAP'][i]:
            bullish = False

    if bullish and bearish:
        vwap_signal =  "Neutral"  # Neither Bullish nor Bearish
    elif bullish:
        vwap_signal =  "Bullish"
    elif bearish:
        vwap_signal =  "Bearish"
    else:
        vwap_signal =  "Neutral"

    if average_rsi > 70:
        rsi_signal = "Overbought"
    elif average_rsi < 30:
        rsi_signal = "Oversold"
    else:
        rsi_signal = "Neutral"

    overbought_signal = (df['Close'] > upper_bb).all()
    oversold_signal = (df['Close'] < lower_bb).all() #This requirement might be too harsh

    if overbought_signal:
        bb_signal = "Overbought"
    elif oversold_signal:
        bb_signal = "Oversold"
    else:
        bb_signal = "Neutral"

    if vwap_signal == "Bullish" and rsi_signal == "Oversold" and bb_signal == "Oversold":
        return "Buy"
    elif vwap_signal == "Bearish" and rsi_signal == "Overbought" and bb_signal == "Overbought":
        return "Sell"
    else:
        return "-"



### 3 - Connect to the market and execute trades

In [4]:
access_token= "cd7e21b015cb734770f5fcfea9da9c9f-49a95de76ed5cab29ee0d33cee5f004d"
accountID = "101-001-27332384-001" #your account ID here
list_of_currency = [Pair.EUR_USD, Pair.EUR_GBP, Pair.USD_JPY, Pair.AUD_USD, Pair.USD_CAD, Pair.CAD_JPY, Pair.NZD_USD]
def get_candles(n, currency):
    client = API(access_token)
    request = InstrumentsCandles(instrument=currency, params={"granularity": Gran.M15, "count": n})
    response = client.request(request)
    candles = response['candles']
    return candles

candles = get_candles(3, Pair.EUR_USD)
candles


[{'complete': True,
  'volume': 1349,
  'time': '2023-11-09T20:00:00.000000000Z',
  'mid': {'o': '1.06676', 'h': '1.06758', 'l': '1.06662', 'c': '1.06742'}},
 {'complete': True,
  'volume': 1231,
  'time': '2023-11-09T20:15:00.000000000Z',
  'mid': {'o': '1.06744', 'h': '1.06750', 'l': '1.06700', 'c': '1.06722'}},
 {'complete': False,
  'volume': 213,
  'time': '2023-11-09T20:30:00.000000000Z',
  'mid': {'o': '1.06719', 'h': '1.06728', 'l': '1.06700', 'c': '1.06700'}}]

In [5]:
def calculate_vwap(data):
    data['VWAP'] = (((data['High'] + data['Low'] + data['Close']) / 3) * data['Volume']).cumsum() / data['Volume'].cumsum()

    

def calculate_bollinger_bands(data, std_dev=2):
    data['SMA'] = data['Close'].mean()
    
    std_dev_values = data['Close'].std()
    data['UpperBB'] = data['SMA'] + (std_dev * std_dev_values)
    data['LowerBB'] = data['SMA'] - (std_dev * std_dev_values)
# Calculate RSI
def calculate_rsi(data):
    data['RSI'] = talib.RSI(data['Close'])

In [6]:
def trading_job(currency, string_currency):
    candles = get_candles(15, currency)
    dfstream = pd.DataFrame(columns=['Open','Close','High','Low', 'Volume'])
    i=0

    for candle in candles:
        dfstream.loc[i, 'Open'] = float(candle['mid']['o'])
        dfstream.loc[i, 'Close'] = float(candle['mid']['c'])
        dfstream.loc[i, 'High'] = float(candle['mid']['h'])
        dfstream.loc[i, 'Low'] = float(candle['mid']['l'])
        dfstream.loc[i, 'Volume'] = float(candle['volume'])
        i += 1

    dfstream['Open'] = dfstream['Open'].astype(float)
    dfstream['Close'] = dfstream['Close'].astype(float)
    dfstream['High'] = dfstream['High'].astype(float)
    dfstream['Low'] = dfstream['Low'].astype(float)
    dfstream['Volume'] = dfstream['Volume'].astype(float)
    calculate_vwap(dfstream)
    calculate_bollinger_bands(dfstream)
    calculate_rsi(dfstream)

    #print(dfstream)
    print(dfstream)
    signal = signal_generator(dfstream)#
    # EXECUTING ORDERS
    print("signal: " + str(signal))
    client = API(access_token)

    SLTPRatio = 2.
    previous_candleR = abs(dfstream['High'].iloc[-2]-dfstream['Low'].iloc[-2])

    SLBuy = float(str(candle['mid']['o']))-previous_candleR
    SLSell = float(str(candle['mid']['o']))+previous_candleR

    TPBuy = float(str(candle['mid']['o']))+previous_candleR*SLTPRatio
    TPSell = float(str(candle['mid']['o']))-previous_candleR*SLTPRatio

    #print(dfstream.iloc[:-1,:])
    #print(TPBuy, "  ", SLBuy, "  ", TPSell, "  ", SLSell)
    #signal = 2
    #Sell
    if signal == "Sell":
        mo = MarketOrderRequest(instrument=string_currency, units=-2000, takeProfitOnFill=TakeProfitDetails(price=TPSell).data, stopLossOnFill=StopLossDetails(price=SLSell).data)
        r = orders.OrderCreate(accountID, data=mo.data)
        rv = client.request(r)
        print(rv)
    #Buy
    elif signal == "Buy":
        mo = MarketOrderRequest(instrument=string_currency, units=2000, takeProfitOnFill=TakeProfitDetails(price=TPBuy).data, stopLossOnFill=StopLossDetails(price=SLBuy).data)
        r = orders.OrderCreate(accountID, data=mo.data)
        rv = client.request(r)
        print(rv)

In [7]:
list_of_currency = [Pair.EUR_USD, Pair.EUR_GBP, Pair.USD_JPY, Pair.AUD_USD, Pair.USD_CAD, Pair.CAD_JPY, Pair.NZD_USD]
list_of_str_currency = ["EUR_USD", "EUR_GBP", "USD_JPY", "AUD_USD","USD_CAD","CAD_JPY","NZD_USD"]

for i in range (len(list_of_str_currency)):
    trading_job(list_of_currency[i],list_of_str_currency[i])


# scheduler = BlockingScheduler()
# for i in range (len(list_of_str_currency)):
#     scheduler.add_job(trading_job, 'cron', args = [list_of_currency[i],list_of_str_currency[i]], day_of_week='mon-fri', hour='00-23', minute='1,11,21,31,41,51', start_date='2022-01-12 12:00:00')
# scheduler.start()

       Open    Close     High      Low  Volume      VWAP      SMA   UpperBB  \
0   1.07098  1.07112  1.07128  1.07074   784.0  1.071047  1.06867  1.071965   
1   1.07114  1.07068  1.07115  1.07051   829.0  1.070910  1.06867  1.071965   
2   1.07066  1.07006  1.07072  1.06999   784.0  1.070696  1.06867  1.071965   
3   1.07004  1.07048  1.07055  1.07004   849.0  1.070607  1.06867  1.071965   
4   1.07050  1.06929  1.07058  1.06726  4290.0  1.069717  1.06867  1.071965   
5   1.06930  1.06984  1.07032  1.06892  2697.0  1.069711  1.06867  1.071965   
6   1.06983  1.06966  1.07014  1.06932  2188.0  1.069710  1.06867  1.071965   
7   1.06967  1.06945  1.06989  1.06929  1509.0  1.069692  1.06867  1.071965   
8   1.06940  1.06760  1.06956  1.06733  3858.0  1.069360  1.06867  1.071965   
9   1.06763  1.06734  1.06773  1.06671  3025.0  1.069055  1.06867  1.071965   
10  1.06736  1.06617  1.06751  1.06603  2196.0  1.068818  1.06867  1.071965   
11  1.06617  1.06674  1.06691  1.06614  1627.0  1.06

In [10]:
da= pd.read_csv("EURUSD_Candlestick_5_M_ASK_30.09.2019-30.09.2022.csv")
da = da[:1000]
signals = []

for i in range(0, len(da)):
    block = da.iloc[i:i+15]
    calculate_vwap(block)
    calculate_bollinger_bands(block)
    calculate_rsi(block)
    block = block.reset_index(drop=True)
    if not block.empty:
        signal = signal_generator(block)
        signals.append(signal)
        print(signals)
print(signals)


/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['VWAP'] = (((data['High'] + data['Low'] + data['Close']) / 3) * data['Volume']).cumsum() / data['Volume'].cumsum()
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['SMA'] = data['Close'].mean()
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:10: SettingWithCopyWar

['-']
['-', '-']
['-', '-', '-']
['-', '-', '-', '-']
['-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-']
['-', '-', '-', '-', '-', '-', 

/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['RSI'] = talib.RSI(data['Close'])
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['VWAP'] = (((data['High'] + data['Low'] + data['Close']) / 3) * data['Volume']).cumsum() / data['Volume'].cumsum()
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:7: SettingWithCop

['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-',

/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['VWAP'] = (((data['High'] + data['Low'] + data['Close']) / 3) * data['Volume']).cumsum() / data['Volume'].cumsum()
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['SMA'] = data['Close'].mean()
/var/folders/k2/1_w7z8xn0fb3dh35c1nd4k5c0000gn/T/ipykernel_55901/2416352855.py:10: SettingWithCopyWar

['-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-', '-',